In [14]:
# from model_avgpool import *
# from dutil import *
# span = [36,102]
# mdl = make_model(output_size=np.diff(span),Nl=6)
# cDATA = load_from_dir('sample/MIDI/jsbach.aug/',span = span,nfile=250)
# print 'Done!'
# mdl.summary()
from dutil import *
mroll = np.load('sample/MIDI/artificial/0.mroll.npy')
print mroll.shape 

/home/shouldsee/.local/lib/python2.7/site-packages/h5py/__init__.py:34: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


is in ipython: 1
[WARN] pymisca.vis_util cannot find network
{'alpha': 0.0, 'negAlpha': True, 'lr': 1.4752850532531738, 'momentum': 1.112934947013855, 'norm': 1.0}
(1053, 128)


In [25]:
from rmidi import *

TESTS finished!!


In [24]:
# util_midi
# ??fluidify
# s = get_ipython()
# get_ipython
import IPython as ip
ip.get_ipython
# getoutput?

In [9]:
# ??util_midi.midi_roll_play
#####
# 50ms chunks
# ??util_midi.mroll_feed
??util_midi.track2midi

In [53]:
def fluidify(fname,sr = 16000,
                SFfile = '/usr/share/sounds/sf2/FluidR3_GM.sf2'):
    outname = '%s.wav' % fname.rsplit('.',1)[0]
    res = get_ipython().getoutput(u'fluidsynth -r {sr} -F {outname} {SFfile} {fname}')
    assert not res.grep('No preset found on*'), "MIDI contains missing preset"
#     res = !fluidsynth {fname}
    return res

def make_test_midi(PROG = 17,fname = 'test.mid'):
#     fname = 'test.mid'
    bname = fname.rsplit('.',1)[0]
    mid = mido.MidiFile(type = 1)

    META_track = mido.MidiTrack()
    META_track += [mido.MetaMessage(type='set_tempo',tempo= 500000,time=0),
              mido.MetaMessage(type = 'smpte_offset', frame_rate=25, hours=0 ,minutes=0 ,seconds=0, frames=1, sub_frames=0,time=0),
              mido.MetaMessage(type = 'time_signature')
             ]
    # <meta message smpte_offset frame_rate=25 hours=0 minutes=0 seconds=0 frames=1 sub_frames=0 time=0>
    # <meta message time_signature numerator=4 denominator=4 clocks_per_click=24 notated_32nd_notes_per_beat=8 time=0>


    mid.tracks.append(META_track)

    track = mido.MidiTrack()
    CHANNEL = 0
#     PROG = 17
    msg = mido.Message(type = 'program_change',channel =CHANNEL, program = PROG-1, time = 50)
    # msg = mido.Message(type = 'note_on',channel =0, program = 42)
    track += [msg]
    for note in range(40,80):
        msg = mido.Message(type = 'note_on',channel = CHANNEL,note = note,time = 5)
        track.append(msg)
        msg = mido.Message(type = 'note_off',channel = CHANNEL,note = note,time =2000)
        track.append(msg)
        pass


    mid.tracks += [track]
    # mid  = clean_this_shit(mid)
    mid.save(fname)
    res = fluidify(fname)
    p = util.piece('%s.wav'%bname)
    p.play()
#     print mid.length
    return mid

def blank_midi():
    mid = mido.MidiFile(type = 1)

    META_track = mido.MidiTrack()
    META_track += [mido.MetaMessage(type='set_tempo',tempo= 500000,time=0),
              mido.MetaMessage(type = 'smpte_offset', frame_rate=25, hours=0 ,minutes=0 ,seconds=0, frames=1, sub_frames=0,time=0),
              mido.MetaMessage(type = 'time_signature')
             ]
    mid.tracks.append(META_track)
#     CHANNEL = 0
    # msg = mido.Message(type = 'note_on',channel =0, program = 42)
#     mid.tracks += [track]
    return mid
def blank_track(CHANNEL = 0,  PROG = 17):
    track = mido.MidiTrack()
    msg = mido.Message(type = 'program_change',channel =CHANNEL, program = PROG-1, time = 50)
    track += [msg]
    return track


#### Make random midi
import random
def track_append_random(track, tick_num,
                       tick_range = None,
                       pitch_range = None,
                       offProb = None):
    if tick_range is None:
        tick_range = (100,800)
    if pitch_range is None:
        pitch_range = range(50,80)
    for msg in track:
        if hasattr(msg,'channel'):
            CHANNEL = msg.channel
        if msg is None:
            raise Exception('Cannot determine channel')
    signal = [0] * 128
    tick_sum = 0
#     min()
    OnOff = ['note_on','note_off']
    onSet = set()
    while tick_sum < tick_num:
        time = random.randrange(*tick_range)
#         switch = random.choice([0,1])
#         if switch:
#             pitch = random.choice([x for x in enumerate(signal) if x])
#         else
#         pitch = random.choice(pitch_range)
        switch = not (random.random() < offProb )
#     np.exp( offProb * (10 - len(S)))
        if switch or not onSet:
            pitch = random.randrange(*pitch_range)
            if pitch in onSet:
                oidx = 1
                onSet.remove(pitch)
            else:
                oidx = 0
                onSet.add(pitch)
        else:
            pitch = random.choice(tuple(onSet))
            onSet.remove(pitch)
            oidx = 1 
                
#         switch= signal[pitch]
#         onlist
        msg = mido.Message(type = OnOff[oidx],channel = CHANNEL,note = pitch,time = time)
#         signal[pitch] = 1 - signal[pitch]
        track.append(msg)
        tick_sum += time
    for pitch in signal:
        if pitch:
            time = 0
            msg = mido.Message(type = OnOff[1],channel = CHANNEL,note = pitch,time = time)
    return track
#     return mid

def random_mid(duration = 48*1000, offProb = 0.5,**kwargs):
    mid  = blank_midi()
#     track = blank_track(0,17)
#     track_append_random( track,duration,offProb = offProb)
#     mid.tracks += [track]
    rinst = lambda :random.choice([62,63,64])
    for ti in range(3):
        track = blank_track(1,rinst())
        track_append_random( track,duration,offProb = offProb,**kwargs)
        mid.tracks += [track]

    return mid
    # mid.print_tracks()
if __name__=='__main__':
    DIR = 'sample/MIDI/artificial'
    for i in range(150):
    #     !rm {DIR}/*.mid
        fname = '%s/%d.mid'%(DIR,i)
    #     fname = '%s/%d.single_mid'%(DIR,i)
        print fname
    #     !rm {fname}
    #     print fname
        mid = random_mid(100*1000,offProb = .7,pitch_range = [60-24,60+48])
        mid.save(fname)

sample/MIDI/artificial/0.mid
sample/MIDI/artificial/1.mid
sample/MIDI/artificial/2.mid
sample/MIDI/artificial/3.mid
sample/MIDI/artificial/4.mid
sample/MIDI/artificial/5.mid
sample/MIDI/artificial/6.mid
sample/MIDI/artificial/7.mid
sample/MIDI/artificial/8.mid
sample/MIDI/artificial/9.mid
sample/MIDI/artificial/10.mid
sample/MIDI/artificial/11.mid
sample/MIDI/artificial/12.mid
sample/MIDI/artificial/13.mid
sample/MIDI/artificial/14.mid
sample/MIDI/artificial/15.mid
sample/MIDI/artificial/16.mid
sample/MIDI/artificial/17.mid
sample/MIDI/artificial/18.mid
sample/MIDI/artificial/19.mid
sample/MIDI/artificial/20.mid
sample/MIDI/artificial/21.mid
sample/MIDI/artificial/22.mid
sample/MIDI/artificial/23.mid
sample/MIDI/artificial/24.mid
sample/MIDI/artificial/25.mid
sample/MIDI/artificial/26.mid
sample/MIDI/artificial/27.mid
sample/MIDI/artificial/28.mid
sample/MIDI/artificial/29.mid
sample/MIDI/artificial/30.mid
sample/MIDI/artificial/31.mid
sample/MIDI/artificial/32.mid
sample/MIDI/artifici

In [54]:
%%time
from rmidi import *
DIR = 'sample/MIDI/artificial/'
DIR_mid2single(DIR,cap = 500, para = 8)
DIR_single2mroll(DIR,cap = 100, para = 7)
DIR_mroll2both(DIR,cap = 500, para = 7)
print 'ALL DONE'

sample/MIDI/artificial/87P0S0.single_mid
sample/MIDI/artificial/137P0S0.single_mid
sample/MIDI/artificial/82P0S0.single_mid
sample/MIDI/artificial/130P0S0.single_mid
sample/MIDI/artificial/76P0S0.single_mid
sample/MIDI/artificial/15P0S0.single_mid
sample/MIDI/artificial/41P0S0.single_mid
sample/MIDI/artificial/10P0S0.single_mid
sample/MIDI/artificial/138P0S0.single_mid
sample/MIDI/artificial/88P0S0.single_mid
sample/MIDI/artificial/126P0S0.single_mid
sample/MIDI/artificial/52P0S0.single_mid
sample/MIDI/artificial/67P0S0.single_mid
sample/MIDI/artificial/37P0S0.single_mid
sample/MIDI/artificial/25P0S0.single_mid
sample/MIDI/artificial/20P0S0.single_mid
sample/MIDI/artificial/78P0S0.single_mid
sample/MIDI/artificial/110P0S0.single_mid
sample/MIDI/artificial/106P0S0.single_mid
sample/MIDI/artificial/83P0S0.single_mid
sample/MIDI/artificial/28P0S0.single_mid
sample/MIDI/artificial/12P0S0.single_mid
sample/MIDI/artificial/101P0S0.single_mid
sample/MIDI/artificial/19P0S0.single_mid
sample/MI

sample/MIDI/artificial/9P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/124P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/67P0S0.single_mid
sample/MIDI/artificial/6P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/144P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/140P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/28P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/96P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/84P0S0.single_mid
[WARN]

sample/MIDI/artificial/143P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/34P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/129P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/61P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/23P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/22P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/110P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/39P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/141P0S0.single_mid
[WA

In [43]:
blank_midi
mid  = blank_midi()
#     track = blank_track(0,17)
#     track_append_random( track,duration,offProb = offProb)
#     mid.tracks += [track]

track = blank_track(2,63)

CHANNEL = track[0].channel
time = 10
dt = 1000
OnOff=['note_on','note_off']
C4 = np.array([60,62,64,65,67,69,71,72])
for pitch in C4:
    msg = mido.Message(type = OnOff[0],channel = CHANNEL,note = pitch,time = 5)
    time += dt
    track.append(msg)
    msg = mido.Message(type = OnOff[1],channel = CHANNEL,note = pitch,time = dt)
    time += dt
    track.append(msg)
for pitch in C4[::-1]:
    msg = mido.Message(type = OnOff[0],channel = CHANNEL,note = pitch,time = 5)
    time += dt
    track.append(msg)
    msg = mido.Message(type = OnOff[1],channel = CHANNEL,note = pitch,time = dt)
    time += dt
    track.append(msg)
#     print time
mid.tracks += [track]
mid.save('test.mid')
fluidify('test.mid')
p = util.piece('test.wav')
# p = util.piece('sample/MIDI/artificial/0.wav')
p.play()
print 

Your browser does not support the audio element.

In [ ]:
fname = 'sample/MIDI/'

In [ ]:
def check_midi(fname,**kwargs):
    assert fname.endswith('mid'), "Must pass a '.mid' file"

    mroll = util_midi.extract_midi_roll(fname, DEBUG=0,**kwargs)
#         SUM = mroll.sum(axis = 1,keepdims = 1)
#         SUM[SUM==0]=1
#         mroll = mroll/SUM
    if mroll is None:
        raise Exception("mroll is None")
    else:
        assert mroll.shape[-1]==128,"make sure mroll is coded in midi"
        
    bname = fname.rsplit('.',1)[0]
#     tim_buffer = timidify(fname)
    tim_buffer = fluidify(fname)
    mroll = np.array(mroll)
    np.save('%s.mroll' % bname, mroll)
    return 1

In [49]:
util.piece('sample/MIDI/artificial/0P0S0.wav').play()

Your browser does not support the audio element.

In [38]:
# ??func_DIR_single2mroll
??check_midi

In [36]:
# import rmidi
??DIR_single2mroll

In [30]:
!rm {DIR}/*

sample/MIDI/artificial/15P0S0.single_mid
sample/MIDI/artificial/137P0S0.single_mid
sample/MIDI/artificial/87P0S0.single_mid
sample/MIDI/artificial/76P0S0.single_mid
sample/MIDI/artificial/138P0S0.single_mid
sample/MIDI/artificial/126P0S0.single_mid
sample/MIDI/artificial/130P0S0.single_mid
sample/MIDI/artificial/82P0S0.single_mid
sample/MIDI/artificial/25P0S0.single_mid
sample/MIDI/artificial/106P0S0.single_mid
sample/MIDI/artificial/78P0S0.single_mid
sample/MIDI/artificial/10P0S0.single_mid
sample/MIDI/artificial/88P0S0.single_mid
sample/MIDI/artificial/52P0S0.single_mid
sample/MIDI/artificial/37P0S0.single_mid
sample/MIDI/artificial/79P0S0.single_mid
sample/MIDI/artificial/92P0S0.single_mid
sample/MIDI/artificial/41P0S0.single_mid
sample/MIDI/artificial/67P0S0.single_mid
sample/MIDI/artificial/19P0S0.single_mid
sample/MIDI/artificial/28P0S0.single_mid
sample/MIDI/artificial/27P0S0.single_mid
sample/MIDI/artificial/20P0S0.single_mid
sample/MIDI/artificial/12P0S0.single_mid
sample/MIDI

sample/MIDI/artificial/124P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/5P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/9P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/67P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/140P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/144P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/28P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/10P0S0.single_mid
sample/MIDI/artificial/84P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
[WARN]

sample/MIDI/artificial/34P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/129P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/26P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/23P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/22P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/110P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/61P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/141P0S0.single_mid
[WARN]:No notes were detected in <meta message set_tempo tempo=500000 time=0>
sample/MIDI/artificial/149P0S0.single_mid
[WA

In [34]:
mid= mido.MidiFile('sample/MIDI/artificial/102P0S0.single_mid')
mid.print_tracks()

=== Track 0
<meta message set_tempo tempo=500000 time=0>
<meta message smpte_offset frame_rate=25 hours=0 minutes=0 seconds=0 frames=0 sub_frames=0 time=0>
<meta message time_signature numerator=4 denominator=2 clocks_per_click=24 notated_32nd_notes_per_beat=8 time=0>
<meta message end_of_track time=0>
=== Track 1
<message program_change channel=1 program=62 time=50>
<message note_on channel=1 note=36 velocity=64 time=587>
<message note_off channel=1 note=36 velocity=64 time=546>
<message note_on channel=1 note=96 velocity=64 time=624>
<message note_off channel=1 note=96 velocity=64 time=618>
<message note_on channel=1 note=96 velocity=64 time=208>
<message note_off channel=1 note=96 velocity=64 time=238>
<message note_on channel=1 note=96 velocity=64 time=260>
<message note_on channel=1 note=36 velocity=64 time=660>
<message note_off channel=1 note=36 velocity=64 time=644>
<message note_off channel=1 note=96 velocity=64 time=653>
<message note_on channel=1 note=36 velocity=64 time=184

In [33]:
mid = make_test_midi()
for p in mid.tracks[-1]:
    print p

Your browser does not support the audio element.

program_change channel=0 program=16 time=50
note_on channel=0 note=40 velocity=64 time=5
note_off channel=0 note=40 velocity=64 time=2000
note_on channel=0 note=41 velocity=64 time=5
note_off channel=0 note=41 velocity=64 time=2000
note_on channel=0 note=42 velocity=64 time=5
note_off channel=0 note=42 velocity=64 time=2000
note_on channel=0 note=43 velocity=64 time=5
note_off channel=0 note=43 velocity=64 time=2000
note_on channel=0 note=44 velocity=64 time=5
note_off channel=0 note=44 velocity=64 time=2000
note_on channel=0 note=45 velocity=64 time=5
note_off channel=0 note=45 velocity=64 time=2000
note_on channel=0 note=46 velocity=64 time=5
note_off channel=0 note=46 velocity=64 time=2000
note_on channel=0 note=47 velocity=64 time=5
note_off channel=0 note=47 velocity=64 time=2000
note_on channel=0 note=48 velocity=64 time=5
note_off channel=0 note=48 velocity=64 time=2000
note_on channel=0 note=49 velocity=64 time=5
note_off channel=0 note=49 velocity=64 time=2000
note_on channel=

In [4]:
# np.load('sample/MIDI/artificial/0.mroll.npy')
xs = util_midi.midi_roll_play(mroll)

array([ 0.00000000e+00,  4.01371902e-01,  7.88703184e-01, ...,
       -3.65129711e-02,  3.41733762e-04,  3.71761347e-02])